![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Systemy Dialogowe </h1>
<h2> 8. <i>Parsing semantyczny z wykorzystaniem technik uczenia maszynowego</i>  [laboratoria]</h2> 
<h3> Marek Kubis (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Parsing semantyczny z wykorzystaniem technik uczenia maszynowego
================================================================

Wprowadzenie
------------
Problem wykrywania slotów i ich wartości w wypowiedziach użytkownika można sformułować jako zadanie
polegające na przewidywaniu dla poszczególnych słów etykiet wskazujących na to czy i do jakiego
slotu dane słowo należy.

> chciałbym zarezerwować stolik na jutro**/day** na godzinę dwunastą**/hour** czterdzieści**/hour** pięć**/hour** na pięć**/size** osób

Granice slotów oznacza się korzystając z wybranego schematu etykietowania.

### Schemat IOB

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |

> chciałbym zarezerwować stolik na jutro**/B-day** na godzinę dwunastą**/B-hour** czterdzieści**/I-hour** pięć**/I-hour** na pięć**/B-size** osób

### Schemat IOBES

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |
| E      | koniec slotu (ending)      |
| S      | pojedyncze słowo (single)  |

> chciałbym zarezerwować stolik na jutro**/S-day** na godzinę dwunastą**/B-hour** czterdzieści**/I-hour** pięć**/E-hour** na pięć**/S-size** osób

Jeżeli dla tak sformułowanego zadania przygotujemy zbiór danych
złożony z wypowiedzi użytkownika z oznaczonymi slotami (tzw. *zbiór uczący*),
to możemy zastosować techniki (nadzorowanego) uczenia maszynowego w celu zbudowania modelu
annotującego wypowiedzi użytkownika etykietami slotów.

Do zbudowania takiego modelu można wykorzystać między innymi:

 1. warunkowe pola losowe (Lafferty i in.; 2001),

 2. rekurencyjne sieci neuronowe, np. sieci LSTM (Hochreiter i Schmidhuber; 1997),

 3. transformery (Vaswani i in., 2017).

Przykład
--------
Skorzystamy ze zbioru danych przygotowanego przez Schustera (2019).

In [ ]:
!mkdir -p l07
%cd l07
!curl -L -C -  https://fb.me/multilingual_task_oriented_data  -o data.zip
!unzip data.zip
%cd ..

Zbiór ten gromadzi wypowiedzi w trzech językach opisane slotami dla dwunastu ram należących do trzech dziedzin `Alarm`, `Reminder` oraz `Weather`. Dane wczytamy korzystając z biblioteki [conllu](https://pypi.org/project/conllu/).

In [1]:
from conllu import parse_incr
fields = ['id', 'form', 'frame', 'slot']

def nolabel2o(line, i):
    return 'O' if line[i] == 'NoLabel' else line[i]

with open('./train_data//train.conllu') as trainfile:
    trainset = list(parse_incr(trainfile, fields=fields, field_parsers={'slot': nolabel2o}))
with open('./train_data//test.conllu') as testfile:
    testset = list(parse_incr(testfile, fields=fields, field_parsers={'slot': nolabel2o}))

Zobaczmy kilka przykładowych wypowiedzi z tego zbioru.

In [21]:
from tabulate import tabulate
tabulate(trainset[26], tablefmt='html')

'<table>\n<tbody>\n<tr><td style="text-align: right;">1</td><td>chciaĹ‚bym</td><td></td><td>O</td></tr>\n<tr><td style="text-align: right;">2</td><td>kupiÄ‡    </td><td></td><td>O</td></tr>\n<tr><td style="text-align: right;">3</td><td>popcorn   </td><td></td><td>O</td></tr>\n</tbody>\n</table>'

In [ ]:
tabulate(trainset[1000], tablefmt='html')

In [ ]:
tabulate(trainset[2000], tablefmt='html')

Na potrzeby prezentacji procesu uczenia w jupyterowym notatniku zawęzimy zbiór danych do początkowych przykładów.

In [ ]:
trainset = trainset[:100]
testset = testset[:100]

Budując model skorzystamy z architektury opartej o rekurencyjne sieci neuronowe
zaimplementowanej w bibliotece [flair](https://github.com/flairNLP/flair) (Akbik i in. 2018).

In [7]:
from flair.data import Corpus, Sentence, Token
from flair.datasets import SentenceDataset
from flair.embeddings import StackedEmbeddings
from flair.embeddings import WordEmbeddings
from flair.embeddings import CharacterEmbeddings
from flair.embeddings import FlairEmbeddings
from flair.models import SequenceTagger
from flair.trainers import ModelTrainer

# determinizacja obliczeń
import random
import torch
random.seed(42)
torch.manual_seed(42)

if torch.cuda.is_available():
    torch.cuda.manual_seed(0)
    torch.cuda.manual_seed_all(0)
    torch.backends.cudnn.enabled = False
    torch.backends.cudnn.benchmark = False
    torch.backends.cudnn.deterministic = True

C:\Users\Adrian\AppData\Roaming\Python\Python37\site-packages\tqdm\auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Dane skonwertujemy do formatu wykorzystywanego przez `flair`, korzystając z następującej funkcji.

In [8]:
def conllu2flair(sentences, label=None):
    fsentences = []

    for sentence in sentences:
        fsentence = Sentence()

        for token in sentence:
            ftoken = Token(token['form'])

            if label:
                ftoken.add_tag(label, token[label])

            fsentence.add_token(ftoken)

        fsentences.append(fsentence)

    return SentenceDataset(fsentences)

corpus = Corpus(train=conllu2flair(trainset, 'slot'), test=conllu2flair(testset, 'slot'))
print(corpus)
tag_dictionary = corpus.make_tag_dictionary(tag_type='slot')
print(tag_dictionary)

Corpus: 194 train + 22 dev + 33 test sentences
Dictionary with 12 tags: <unk>, O, B-time, I-time, B-area, I-area, B-quantity, B-date, I-quantity, I-date, <START>, <STOP>


Nasz model będzie wykorzystywał wektorowe reprezentacje słów (zob. [Word Embeddings](https://github.com/flairNLP/flair/blob/master/resources/docs/TUTORIAL_3_WORD_EMBEDDING.md)).

In [9]:
embedding_types = [
    WordEmbeddings('pl'),
    FlairEmbeddings('polish-forward'),
    FlairEmbeddings('polish-backward'),
    CharacterEmbeddings(),
]

embeddings = StackedEmbeddings(embeddings=embedding_types)
tagger = SequenceTagger(hidden_size=256, embeddings=embeddings,
                        tag_dictionary=tag_dictionary,
                        tag_type='slot', use_crf=True)

2022-05-17 23:51:31,428 https://flair.informatik.hu-berlin.de/resources/embeddings/token/pl-wiki-fasttext-300d-1M.vectors.npy not found in cache, downloading to C:\Users\Adrian\AppData\Local\Temp\tmpdtf6je0q


100%|██████████| 1199998928/1199998928 [00:38<00:00, 31059047.54B/s]

2022-05-17 23:52:10,221 copying C:\Users\Adrian\AppData\Local\Temp\tmpdtf6je0q to cache at C:\Users\Adrian\.flair\embeddings\pl-wiki-fasttext-300d-1M.vectors.npy


2022-05-17 23:52:11,581 removing temp file C:\Users\Adrian\AppData\Local\Temp\tmpdtf6je0q
2022-05-17 23:52:11,834 https://flair.informatik.hu-berlin.de/resources/embeddings/token/pl-wiki-fasttext-300d-1M not found in cache, downloading to C:\Users\Adrian\AppData\Local\Temp\tmpncdt74ud


100%|██████████| 40874795/40874795 [00:01<00:00, 25496548.48B/s]

...

2022-05-17 23:52:24,338 copying C:\Users\Adrian\AppData\Local\Temp\tmp6okeka8n to cache at C:\Users\Adrian\.flair\embeddings\lm-polish-forward-v0.2.pt


2022-05-17 23:52:24,435 removing temp file C:\Users\Adrian\AppData\Local\Temp\tmp6okeka8n
2022-05-17 23:52:24,857 https://flair.informatik.hu-berlin.de/resources/embeddings/flair/lm-polish-backward-v0.2.pt not found in cache, downloading to C:\Users\Adrian\AppData\Local\Temp\tmp_6ut1zi9


100%|██████████| 84244196/84244196 [00:02<00:00, 35815492.94B/s]

2022-05-17 23:52:27,375 copying C:\Users\Adrian\AppData\Local\Temp\tmp_6ut1zi9 to cache at C:\Users\Adrian\.flair\embeddings\lm-polish-backward-v0.2.pt


2022-05-17 23:52:27,460 removing temp file C:\Users\Adrian\AppData\Local\Temp\tmp_6ut1zi9


Zobaczmy jak wygląda architektura sieci neuronowej, która będzie odpowiedzialna za przewidywanie
slotów w wypowiedziach.

In [10]:
print(tagger)

SequenceTagger(
  (embeddings): StackedEmbeddings(
    (list_embedding_0): WordEmbeddings('pl')
    (list_embedding_1): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_2): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_3): CharacterEmbeddings(
      (char_embedding): Embedding(275, 25)
      (char_rnn): LSTM(25, 25, bidirectional=True)
    )
  )
  (word_dropout): WordDropout(p=0.05)
  (locked_dropout): LockedDropout(p=0.5)
  (embedding2nn): Linear(in_features=4446, out_features=4446, bias=True)
  (rnn): LSTM(4446, 256, batch_first=True, bidirectiona

Wykonamy dziesięć iteracji (epok) uczenia a wynikowy model zapiszemy w katalogu `slot-model`.

In [11]:
trainer = ModelTrainer(tagger, corpus)
trainer.train('slot-model',
              learning_rate=0.1,
              mini_batch_size=32,
              max_epochs=10,
              train_with_dev=False)

2022-05-17 23:52:57,432 ----------------------------------------------------------------------------------------------------
2022-05-17 23:52:57,433 Model: "SequenceTagger(
  (embeddings): StackedEmbeddings(
    (list_embedding_0): WordEmbeddings('pl')
    (list_embedding_1): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_2): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_3): CharacterEmbeddings(
      (char_embedding): Embedding(275, 25)
      (char_rnn): LSTM(25, 25, bidirectional=True)
    )
  )
  (word_dropout): WordDropout(p=0.05)
  (locked_dr

{'test_score': 0.4,
 'dev_score_history': [0.2,
  0.36363636363636365,
  0.3076923076923077,
  0.28571428571428575,
  0.3076923076923077,
  0.28571428571428575,
  0.28571428571428575,
  0.28571428571428575,
  0.3076923076923077,
  0.3076923076923077],
 'train_loss_history': [8.107216443334307,
  2.19215042250497,
  1.735515492303031,
  1.5392142619405473,
  2.721130439213344,
  1.6617201566696167,
  1.460041948727199,
  1.2011338983263289,
  1.1026092597416468,
  1.012676673276084],
 'dev_loss_history': [3.991352081298828,
  3.9842920303344727,
  3.3194284439086914,
  2.8986825942993164,
  2.766446590423584,
  2.2595832347869873,
  2.200728416442871,
  2.4227261543273926,
  2.1707162857055664,
  1.9863343238830566]}

Jakość wyuczonego modelu możemy ocenić, korzystając z zaraportowanych powyżej metryk, tj.:

 - *tp (true positives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fp (false positives)*

   > liczba słów nieoznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fn (false negatives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, którym model nie nadał etykiety $e$

 - *precision*

   > $$\frac{tp}{tp + fp}$$

 - *recall*

   > $$\frac{tp}{tp + fn}$$

 - $F_1$

   > $$\frac{2 \cdot precision \cdot recall}{precision + recall}$$

 - *micro* $F_1$

   > $F_1$ w którym $tp$, $fp$ i $fn$ są liczone łącznie dla wszystkich etykiet, tj. $tp = \sum_{e}{{tp}_e}$, $fn = \sum_{e}{{fn}_e}$, $fp = \sum_{e}{{fp}_e}$

 - *macro* $F_1$

   > średnia arytmetyczna z $F_1$ obliczonych dla poszczególnych etykiet z osobna.

Wyuczony model możemy wczytać z pliku korzystając z metody `load`.

In [22]:
model = SequenceTagger.load('slot-model/final-model.pt')

2022-05-17 23:57:03,014 loading file slot-model/final-model.pt


Wczytany model możemy wykorzystać do przewidywania slotów w wypowiedziach użytkownika, korzystając
z przedstawionej poniżej funkcji `predict`.

In [23]:
def predict(model, sentence):
    csentence = [{'form': word} for word in sentence]
    fsentence = conllu2flair([csentence])[0]
    model.predict(fsentence)
    return [(token, ftoken.get_tag('slot').value) for token, ftoken in zip(sentence, fsentence)]


Jak pokazuje przykład poniżej model wyuczony tylko na 100 przykładach popełnia w dosyć prostej
wypowiedzi błąd etykietując słowo `alarm` tagiem `B-weather/noun`.

In [28]:
tabulate(predict(model, 'chciałbym zarezerwować 2 bilety na batman na 19:30 na środku z tyłun po prawej i po lewej nie chce z przodu'.split()), tablefmt='html')

'<table>\n<tbody>\n<tr><td>chciałbym   </td><td>O         </td></tr>\n<tr><td>zarezerwować</td><td>O         </td></tr>\n<tr><td>2           </td><td>B-quantity</td></tr>\n<tr><td>bilety      </td><td>O         </td></tr>\n<tr><td>na          </td><td>O         </td></tr>\n<tr><td>batman      </td><td>O         </td></tr>\n<tr><td>na          </td><td>O         </td></tr>\n<tr><td>19:30       </td><td>B-quantity</td></tr>\n<tr><td>na          </td><td>O         </td></tr>\n<tr><td>środku      </td><td>O         </td></tr>\n<tr><td>z           </td><td>O         </td></tr>\n<tr><td>tyłun       </td><td>O         </td></tr>\n<tr><td>po          </td><td>O         </td></tr>\n<tr><td>prawej      </td><td>O         </td></tr>\n<tr><td>i           </td><td>O         </td></tr>\n<tr><td>po          </td><td>O         </td></tr>\n<tr><td>lewej       </td><td>O         </td></tr>\n<tr><td>nie         </td><td>O         </td></tr>\n<tr><td>chce        </td><td>O         </td></tr>\n<tr><td>z           </td><td>O         </td></tr>\n<tr><td>przodu      </td><td>O         </td></tr>\n</tbody>\n</table>'

Literatura
----------
 1. Sebastian Schuster, Sonal Gupta, Rushin Shah, Mike Lewis, Cross-lingual Transfer Learning for Multilingual Task Oriented Dialog. NAACL-HLT (1) 2019, pp. 3795-3805
 2. John D. Lafferty, Andrew McCallum, and Fernando C. N. Pereira. 2001. Conditional Random Fields: Probabilistic Models for Segmenting and Labeling Sequence Data. In Proceedings of the Eighteenth International Conference on Machine Learning (ICML '01). Morgan Kaufmann Publishers Inc., San Francisco, CA, USA, 282–289, https://repository.upenn.edu/cgi/viewcontent.cgi?article=1162&context=cis_papers
 3. Sepp Hochreiter and Jürgen Schmidhuber. 1997. Long Short-Term Memory. Neural Comput. 9, 8 (November 15, 1997), 1735–1780, https://doi.org/10.1162/neco.1997.9.8.1735
 4. Ashish Vaswani, Noam Shazeer, Niki Parmar, Jakob Uszkoreit, Llion Jones, Aidan N. Gomez, Lukasz Kaiser, Illia Polosukhin, Attention is All you Need, NIPS 2017, pp. 5998-6008, https://arxiv.org/abs/1706.03762
 5. Alan Akbik, Duncan Blythe, Roland Vollgraf, Contextual String Embeddings for Sequence Labeling, Proceedings of the 27th International Conference on Computational Linguistics, pp. 1638–1649, https://www.aclweb.org/anthology/C18-1139.pdf
